### Yellow Taxi Data
Extracting, Cleaning and Loading Yellow Taxi Data

Creating Fact table and registering as Global Temporary view

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.functions import col

In [0]:
dbutils.widgets.text("ProcessMonth", "201812", "Process Month (yyyymm)")

In [0]:
processMonth = dbutils.widgets.get("ProcessMonth")

In [0]:
print("Starting to extract Yellow Taxi data")

yellowTaxiTripDataDF = spark \
                    .read \
                    .option("header", "true") \
                    .option("inferSchema", "true") \
                    .csv("dbfs:/mnt/dataadls/YellowTaxiTripData_201812.csv")

# display(yellowTaxiTripDataDF.dtypes)

yellowTaxiTripDataDF = yellowTaxiTripDataDF \
                            .where("passenger_count > 0") \
                            .filter("trip_distance > 0.0") \
                            .na.drop(subset=("PULocationID", "DOLocationID"),how="any") \
                            .na.fill(value=5,subset=["payment_type"]) \
                            .na.fill(value=1,subset=["RatecodeID"]) \
                            .dropDuplicates()                              

print("Extracted and cleaned Yellow Taxi data")

Starting to extract Yellow Taxi data
Extracted and cleaned Yellow Taxi data

In [0]:
# yellowTaxiTripDataDF.printSchema

In [0]:
# display(yellowTaxiTripDataDF)

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount 2 2018-12-01T00:11:18.000+0000 2018-12-01T00:33:28.000+0000 1 3.72 1 N 141 90 1 16.0 0.5 0.5 2.6 0.0 0.3 19.9 1 2018-12-01T00:00:12.000+0000 2018-12-01T00:13:49.000+0000 1 2.4 1 N 162 158 1 11.0 0.5 0.5 3.05 0.0 0.3 15.35 2 2018-12-01T00:34:47.000+0000 2018-12-01T01:08:51.000+0000 2 6.21 1 N 113 263 2 25.0 0.5 0.5 0.0 0.0 0.3 26.3 2 2018-12-01T00:37:45.000+0000 2018-12-01T00:49:17.000+0000 1 2.66 1 N 230 238 1 11.5 0.5 0.5 3.2 0.0 0.3 16.0 1 2018-12-01T00:08:23.000+0000 2018-12-01T00:11:07.000+0000 1 0.6 1 Y 262 263 2 4.5 0.5 0.5 0.0 0.0 0.3 5.8 2 2018-12-01T00:13:39.000+0000 2018-12-01T00:25:36.000+0000 2 2.85 1 N 144 229 2 11.0 0.5 0.5 0.0 0.0 0.3 12.3 2 2018-12-01T00:51:30.000+0000 2018-12-01T00:57:38.000+0000 1 1.15 1 N 229 140 1 6.5 0.5 0.5 1.0 0.0 0.3 8.8 2 2018-12-01T00:27:43.000+0000 2018-12-01T00:38:56.000+0000 2 2.76 1 N 148 229 1 10.5 0.5 0.5 2.0 0.0 0.3 13.8 2 2018-12-01T00:30:07.000+0000 2018-12-01T00:43:14.000+0000 1 2.63 1 N 142 107 1 11.0 0.5 0.5 1.0 0.0 0.3 13.3 1 2018-12-01T00:10:36.000+0000 2018-12-01T00:19:30.000+0000 1 1.8 1 N 181 33 1 8.5 0.5 0.5 1.95 0.0 0.3 11.75 1 2018-12-01T00:13:37.000+0000 2018-12-01T00:24:24.000+0000 1 1.2 1 N 230 229 2 8.0 0.5 0.5 0.0 0.0 0.3 9.3 2 2018-12-01T00:14:43.000+0000 2018-12-01T00:19:26.000+0000 2 0.92 1 N 170 229 1 5.5 0.5 0.5 1.36 0.0 0.3 8.16 2 2018-12-01T00:55:05.000+0000 2018-12-01T01:19:03.000+0000 1 3.29 1 N 161 148 2 16.0 0.5 0.5 0.0 0.0 0.3 17.3 2 2018-12-01T00:12:37.000+0000 2018-12-01T00:15:21.000+0000 1 0.51 1 N 152 152 1 4.0 0.5 0.5 1.06 0.0 0.3 6.36 2 2018-12-01T00:52:21.000+0000 2018-12-01T00:57:05.000+0000 1 0.8 1 N 144 249 1 5.5 0.5 0.5 1.36 0.0 0.3 8.16 2 2018-12-01T00:17:24.000+0000 2018-12-01T00:21:35.000+0000 1 1.28 1 N 137 229 1 5.5 0.5 0.5 1.0 0.0 0.3 7.8 2 2018-12-01T00:02:49.000+0000 2018-12-01T00:11:28.000+0000 5 2.22 1 N 263 162 1 9.0 0.5 0.5 2.06 0.0 0.3 12.36 2 2018-12-01T00:39:35.000+0000 2018-12-01T00:51:58.000+0000 1 2.06 1 N 158 100 1 10.0 0.5 0.5 2.26 0.0 0.3 13.56 2 2018-11-30T23:08:18.000+0000 2018-11-30T23:18:43.000+0000 1 2.04 1 N 239 41 1 9.0 0.5 0.5 2.58 0.0 0.3 12.88 2 2018-12-01T00:44:09.000+0000 2018-12-01T01:09:04.000+0000 5 6.05 1 N 170 255 1 23.0 0.5 0.5 4.0 0.0 0.3 28.3 2 2018-12-01T00:43:44.000+0000 2018-12-01T00:47:55.000+0000 1 0.94 1 N 68 246 2 5.0 0.5 0.5 0.0 0.0 0.3 6.3 2 2018-12-01T00:25:16.000+0000 2018-12-01T00:50:59.000+0000 1 3.9 1 N 79 112 1 20.5 0.5 0.5 3.0 0.0 0.3 24.8 2 2018-12-01T00:08:51.000+0000 2018-12-01T00:21:55.000+0000 1 2.33 1 N 65 54 1 11.0 0.5 0.5 2.46 0.0 0.3 14.76 1 2018-12-01T00:12:39.000+0000 2018-12-01T00:39:26.000+0000 1 4.2 1 N 79 33 1 19.0 0.5 0.5 4.05 0.0 0.3 24.35 1 2018-12-01T00:18:29.000+0000 2018-12-01T00:29:17.000+0000 3 1.1 1 N 264 264 1 8.5 0.5 0.5 1.0 0.0 0.3 10.8 1 2018-12-01T00:59:51.000+0000 2018-12-01T01:08:32.000+0000 4 2.1 1 N 75 238 1 9.0 0.5 0.5 0.0 0.0 0.3 10.3 2 2018-11-30T23:54:15.000+0000 2018-12-01T00:09:51.000+0000 3 3.22 1 N 164 236 1 13.0 0.5 0.5 2.86 0.0 0.3 17.16 2 2018-12-01T00:07:32.000+0000 2018-12-01T00:11:17.000+0000 1 1.02 1 N 161 186 1 5.0 0.5 0.5 1.58 0.0 0.3 7.88 2 2018-12-01T00:47:52.000+0000 2018-12-01T01:27:58.000+0000 1 7.73 1 N 68 7 1 30.5 0.5 0.5 0.0 0.0 0.3 31.8 1 2018-12-01T00:23:28.000+0000 2018-12-01T01:01:23.000+0000 2 4.4 1 N 249 97 1 24.5 0.5 0.5 6.45 0.0 0.3 32.25 2 2018-12-01T00:36:54.000+0000 2018-12-01T00:56:45.000+0000 3 5.01 1 N 88 181 1 17.5 0.5 0.5 3.76 0.0 0.3 22.56 1 2018-12-01T00:25:20.000+0000 2018-12-01T00:36:38.000+0000 1 2.0 1 N 114 13 1 10.0 0.5 0.5 2.25 0.0 0.3 13.55 1 2018-12-01T00:47:09.000+0000 2018-12-01T00:50:01.000+0000 1 0.6 1 N 48 48 1 4.0 0.5 0.5 1.5 0.0 0.3 6.8 1 2018-12-01T00:34:23.000+0000 2018-12-01T00:43:28.000+0000 1 0.8 1 N 162 233 2 7.0 0.5 0.5 0.0 0.0 0.3 8.3 1 2018-12-01T00:15

In [0]:
print("Starting transformation on Yellow Taxi data")

# Apply transformations to Yellow taxi data
yellowTaxiTripDataDF = yellowTaxiTripDataDF \
                            .select(
                                col("VendorID"),
                                col("passenger_count").alias("PassengerCount"),
                                col("trip_distance").alias("TripDistance"),
                                col("tpep_pickup_datetime").alias("PickupTime"),                          
                                col("tpep_dropoff_datetime").alias("DropTime"), 
                                col("PUlocationID").alias("PickupLocationId"), 
                                col("DOlocationID").alias("DropLocationId"), 
                                col("RatecodeID"), 
                                col("total_amount").alias("TotalAmount"),
                                col("payment_type").alias("PaymentType")
                               ) \
                        .withColumn("TripYear", year("PickupTime")) \
                        .withColumn("TripMonth", month("PickupTime")) \
                        .withColumn("TripDay", dayofmonth("PickupTime")) \
                        .withColumn("TripTimeInMinutes", 
                                        round(
                                                (unix_timestamp("DropTime") - unix_timestamp("PickupTime")) 
                                                    / 60
                                             )
                                   ) \
                        .withColumn("TripType", 
                                        when(col("RatecodeID") == 6,"SharedTrip").otherwise("SoloTrip")
                                   ) \
                        .drop("RatecodeID")

print("Applied transformations on Yellow Taxi data")

Starting transformation on Yellow Taxi data
Applied transformations on Yellow Taxi data

In [0]:
yellowTaxiTripDataDF.createOrReplaceGlobalTempView("FactYellowTaxiTripData")

print("Saved Yellow Taxi fact as a global temp view")

Saved Yellow Taxi fact as a global temp view

In [0]:
print("Starting to save Yellow Taxi dataframe as a fact and unmanaged table")

# Store the DataFrame as an Unmanaged Table
yellowTaxiTripDataDF \
    .write \
    .mode("overwrite") \
    .option("path", "/mnt/datalake/DimensionalModel/Facts/YellowTaxiFact.parquet") \
    .saveAsTable("TaxiServiceWarehouse.FactYellowTaxiTripData") 

print("Saved Yellow Taxi dataframe as a fact and unmanaged table")

Starting to save Yellow Taxi dataframe as a fact and unmanaged table
Saved Yellow Taxi dataframe as a fact and unmanaged table

In [0]:
dbutils.notebook.exit("Success")